# Alphalens and Pyfolio integration

Alphalens can simulate the performance of a portfolio where the factor values are use to weight stocks. Once the portfolio is built, it can be analyzed by Pyfolio. For details on how this portfolio is built see:
- alphalens.performance.factor_returns
- alphalens.performance.cumulative_returns 
- alphalens.performance.create_pyfolio_input

In [1]:
# %pylab inline --no-import-all
import alphalens
import pyfolio
import pandas as pd
import numpy as np
import datetime

First load some stocks data

# 参数

In [2]:
lookahead_bias_days = 5
start_date = "2019-01-01"
end_date = '2020-07-15'

# 数据

In [3]:
from pathlib import Path

In [4]:
fp_sector = Path('sector.pkl')
fp_pricing = Path('b_open.pkl')

In [5]:
from zipline.research import get_pricing, get_sector_mappings

In [6]:
if not fp_sector.exists():
    # asset -> sector name
    sector_mappings = get_sector_mappings()
    tickers = np.random.choice(list(sector_mappings.keys()), 100)
    sector_mappings = {k:sector_mappings[k] for k in tickers}
    s = pd.Series(sector_mappings)
    s.to_pickle(str(fp_sector))
    
sector_mappings = pd.read_pickle(str(fp_sector)).to_dict()

In [7]:
if not fp_pricing.exists():
    pricing = get_pricing(sector_mappings.keys(), start_date, end_date, fields='b_open')
    pricing.to_pickle(str(fp_pricing))
    
pricing = pd.read_pickle(str(fp_pricing))

In [8]:
factor = -pricing.pct_change(lookahead_bias_days)
# introduce look-ahead bias and make the factor predictive
# factor = predictive_factor.shift(-lookahead_bias_days)
factor = factor.stack()
factor.index = factor.index.set_names(['date', 'asset'])

We'll compute a simple mean reversion factor looking at recent stocks performance: stocks that performed well in the last 5 days will have high rank and vice versa.

The pricing data passed to alphalens should contain the entry price for the assets so it must reflect the next available price after a factor value was observed at a given timestamp. Those prices must not be used in the calculation of the factor values for that time. Always double check to ensure you are not introducing lookahead bias to your study.

The pricing data must also contain the exit price for the assets, for period 1 the price at the next timestamp will be used, for period 2 the price after 2 timestats will be used and so on.

There are no restrinctions/assumptions on the time frequencies a factor should be computed at and neither on the specific time a factor should be traded (trading at the open vs trading at the close vs intraday trading), it is only required that factor and price DataFrames are properly aligned given the rules above.

In our example, before the trading starts every day, we observe yesterday factor values. The price we pass to alphalens is the next available price after that factor observation: the daily open price that will be used as assets entry price. Also, we are not adding additional prices so the assets exit price will be the following days open prices (how many days depends on 'periods' argument). The retuns computed by Alphalens will therefore based on assets open prices.

In [9]:
pricing = pricing.iloc[1:]
pricing.head()

四方精创(300468)  华纺股份(600448)  开尔新材(300234)  \
b_open                                                                
2019-01-03 00:00:00+00:00        14.407         5.125        10.730   
2019-01-04 00:00:00+00:00        14.223         5.208        10.692   
2019-01-07 00:00:00+00:00        14.906         5.233        10.972   
2019-01-08 00:00:00+00:00        15.037         5.158        11.082   
2019-01-09 00:00:00+00:00        15.051         5.150        11.268   

                           云天化(600096)  中国核电(601985)  光弘科技(300735)  \
b_open                                                               
2019-01-03 00:00:00+00:00         8.53         5.400         8.816   
2019-01-04 00:00:00+00:00         8.39         5.371         8.189   
2019-01-07 00:00:00+00:00         8.65         5.469         8.693   
2019-01-08 00:00:00+00:00         8.75         5.547         8.977   
2019-01-09 00:00:00+00:00         8.72         5.547         9.261   

                           宇环数控(002903)  优刻得(688158)  火炬电子(603678)  \
b_open                                                               
2019-01-03 00:00:00+00:00        25.633          NaN        38.046   
2019-01-04 00:00:00+00:00        24.322          NaN        38.579   
2019-01-07 00:00:00+00:00        25.594          NaN        40.881   
2019-01-08 00:00:00+00:00        25.822          NaN        42.639   
2019-01-09 00:00:00+00:00        25.762          NaN        41.967   

                           久远银海(002777)  ...  森霸传感(300701)  新劲刚(300629)  \
b_open                                   ...                              
2019-01-03 00:00:00+00:00        25.432  ...        20.982       23.146   
2019-01-04 00:00:00+00:00        25.638  ...        20.121       23.056   
2019-01-07 00:00:00+00:00        27.123  ...        21.449       25.495   
2019-01-08 00:00:00+00:00        27.465  ...        21.581       28.123   
2019-01-09 00:00:00+00:00        27.356  ...        21.423       26.664   

                           昊海生科(688366)  南天信息(000948)  上海雅仕(603329)  \
b_open                                                                
2019-01-03 00:00:00+00:00           NaN         9.103        15.338   
2019-01-04 00:00:00+00:00           NaN         8.957        14.993   
2019-01-07 00:00:00+00:00           NaN         9.394        15.535   
2019-01-08 00:00:00+00:00           NaN         9.456        15.772   
2019-01-09 00:00:00+00:00           NaN         9.433        15.811   

                           安宁股份(002978)  益佰制药(600594)  威创股份(002308)  \
b_open                                                                
2019-01-03 00:00:00+00:00           NaN        58.343         19.28   
2019-01-04 00:00:00+00:00           NaN        58.125         19.24   
2019-01-07 00:00:00+00:00           NaN        60.262         20.19   
2019-01-08 00:00:00+00:00           NaN        60.793         21.23   
2019-01-09 00:00:00+00:00           NaN        60.793         20.88   

                           凯发电气(300407)  中电环保(300172)  
b_open                                                 
2019-01-03 00:00:00+00:00        30.053        27.323  
2019-01-04 00:00:00+00:00        28.400        27.274  
2019-01-07 00:00:00+00:00        31.337        28.001  
2019-01-08 00:00:00+00:00        31.865        28.050  
2019-01-09 00:00:00+00:00        32.064        28.364  

[5 rows x 100 columns]

# Prepare data and run Alphalens

Pyfolio wants timezone set to UTC otherwise it refuses to work

In [10]:
# 验证 tz == 'UTC'
pricing.index.tz

<UTC>

In [11]:
factor.index.levels[0].tz

<UTC>

In [12]:
factor_data = alphalens.utils.get_clean_factor_and_forward_returns(factor,
                                                                   pricing,
                                                                   periods=(1, 3, 5),
                                                                   quantiles=5,
                                                                   bins=None)

Dropped 1.4% entries from factor data: 1.4% in forward returns computation and 0.0% in binning phase (set max_loss=0 to see potentially suppressed Exceptions).
max_loss is 35.0%, not exceeded: OK!


In [13]:
alphalens.tears.create_summary_tear_sheet(factor_data)

# Prepare data for Pyfolio

We can see in Alphalens analysis that quantiles 1 and 5 are the most predictive so we'll build a portfolio data using only those quantiles.

In [14]:
pf_returns, pf_positions, pf_benchmark = \
    alphalens.performance.create_pyfolio_input(factor_data,
                                               period='1D',
                                               capital=100000,
                                               long_short=True,
                                               group_neutral=False,
                                               equal_weight=True,
                                               quantiles=[1,5],
                                               groups=None,
                                               benchmark_period='1D')

Now that we have prepared the data we can run Pyfolio functions

In [15]:
pyfolio.tears.create_full_tear_sheet(pf_returns,
                                     positions=pf_positions,
                                     benchmark_rets=pf_benchmark)

## Analyzing subsets of data

Sometimes it might be useful to analyze subets of your factor data, for example it could be interesting to see the comparison of your factor in different days of the week. Below we'll see how to select and analyze factor data corresponding to Mondays, the positions will be held the for a period of 5 days

In [16]:
monday_factor_data = factor_data[ factor_data.index.get_level_values('date').weekday == 0 ]

In [17]:
pf_returns, pf_positions, pf_benchmark = \
    alphalens.performance.create_pyfolio_input(monday_factor_data,
                                               period='5D',
                                               capital=100000,
                                               long_short=True,
                                               group_neutral=False,
                                               equal_weight=True,
                                               quantiles=[1,5],
                                               groups=None,
                                               benchmark_period='1D')

In [18]:
pyfolio.tears.create_full_tear_sheet(pf_returns,
                                     positions=pf_positions,
                                     benchmark_rets=pf_benchmark)